<a href="https://colab.research.google.com/github/krjohnn/LU-VTL-25m/blob/main/notebooks/MSP/speech_recognition.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Runas atpazīšana

In [1]:
# Pārbauda GPU pieejamību un statusu
!nvidia-smi

# Instalē nepieciešamās izpildlaika bibliotēkas
!pip install transformers[torch] yt-dlp gradio jiwer openai-whisper diff-match-patch

Wed Jan 21 19:14:13 2026       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 550.54.15              Driver Version: 550.54.15      CUDA Version: 12.4     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  Tesla T4                       Off |   00000000:00:04.0 Off |                    0 |
| N/A   36C    P8              9W /   70W |       0MiB /  15360MiB |      0%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

In [2]:
from transformers import pipeline
from IPython.display import Audio, display, HTML
import jiwer
import whisper
from whisper.tokenizer import get_tokenizer
from diff_match_patch import diff_match_patch
import re
from itertools import zip_longest
import gradio as gr

In [3]:
# Audio paraugs - Pasaules diktāta latviešu valodā lejupielāde no GitGub
!wget https://github.com/LUMII-AILab/NLP_Course/raw/refs/heads/main/notebooks/resources/ASR/diktats2024.mp3

# Audio paraugs - LTV ziņu fragmenta lejupielāde no YouTube
!yt-dlp -x --audio-format mp3 --download-sections "*00:00:00-00:00:31" -o "zinas1.%(ext)s" "https://www.youtube.com/watch?v=D5jMv2zBmbc"
# Ja tiek izmestas kļūdas "HTTP error 403 Forbidden" un "ffmpeg exited with code 1",
# izvēlieties citu YouTube video, atbilstoši precizējot lejuplādējamo laika intervālu

--2026-01-21 19:15:51--  https://github.com/LUMII-AILab/NLP_Course/raw/refs/heads/main/notebooks/resources/ASR/diktats2024.mp3
Resolving github.com (github.com)... 140.82.116.3
Connecting to github.com (github.com)|140.82.116.3|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/LUMII-AILab/NLP_Course/refs/heads/main/notebooks/resources/ASR/diktats2024.mp3 [following]
--2026-01-21 19:15:51--  https://raw.githubusercontent.com/LUMII-AILab/NLP_Course/refs/heads/main/notebooks/resources/ASR/diktats2024.mp3
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.109.133, 185.199.108.133, 185.199.111.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.109.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 4000748 (3.8M) [audio/mpeg]
Saving to: ‘diktats2024.mp3’

diktats2024.mp3     100%[===================>]   3.81M  --.-KB/s    in 0.05s   

2026-01-21 

In [4]:
# Audio paraugu priekšskatīšana
display(Audio('diktats2024.mp3'))
display(Audio('zinas1.mp3'))

In [5]:
# Palīgfunkcijas transkripciju apstrādei, sastatīšanai

def normalize(t):
    t = t.lower()
    t = re.sub(r'\W', ' ', t)
    t = re.sub(r'\s+', ' ', t)
    t = t.strip()
    return t

# Rakstzīmju līmeņa diff-match-patch:
# ievietošana un dzēšana, lai pred(icted) sastatītu ar ref(erence)
def show_aligment(pred, ref):
    dmp = diff_match_patch()
    diffs = dmp.diff_main(pred, ref)
    dmp.diff_cleanupSemantic(diffs)

    css = """
      <style>
        .d del{background:#ffe6e6;color:#7a1c1c;text-decoration:none;}
        .d ins{background:#e6ffed;color:#14532d;text-decoration:none;}
      </style>
    """
    esc = lambda s: s.replace("&","&amp;").replace("<","&lt;").replace(">","&gt;")

    out = []
    for op, data in diffs:
        s = esc(data)
        if op == 0:   out.append(s)
        if op == -1:  out.append(f"<del>{s}</del>")
        if op == 1:   out.append(f"<ins>{s}</ins>")

    display(HTML(css + "<div class='d'>" + "".join(out) + "</div>"))

def show_wer_alignment(w):
  import html as _html
  boxes = []

  for a in w.alignments[0]:
      hyp_slice = w.hypotheses[0][a.hyp_start_idx:a.hyp_end_idx]
      ref_slice = w.references[0][a.ref_start_idx:a.ref_end_idx]

      for hyp_tok, ref_tok in zip_longest(hyp_slice, ref_slice, fillvalue=''):
          hyp = _html.escape(hyp_tok or '∅')
          ref = _html.escape(ref_tok or '∅')
          t = a.type

          boxes.append(f"""
            <div class="align-box align-{t}">
              <div class="hyp">{hyp}</div>
              <div class="ref">{ref if t != 'equal' else '&nbsp;'}</div>
            </div>
          """)

  html = """
    <style>
      # .align-wrap { font-family: monospace; }
      .align-box {
        display: inline-block;
        border: 1px solid #eee;
      }
      .align-insert     { background: #89ff7d; }
      .align-delete     { background: #ff9898; }
      .align-substitute { background: #fffaf0; }
    </style>
    <div class="align-wrap">
    """ + "\n".join(boxes) + "</div>"

  display(HTML(html))

def evaluate(ref, pred, normalizer=normalize):
    if normalizer:
        ref = normalizer(ref)
        pred = normalizer(pred)

    w = jiwer.process_words(ref, pred)
    c = jiwer.process_characters(ref, pred)

    print('WER', w.wer, "hits", w.hits, "subs", w.substitutions, "dels", w.deletions, "ins", w.insertions, "n_ref", sum(len(x) for x in w.references), "n_hyp", sum(len(x) for x in w.hypotheses))
    print('CER', c.cer, "hits", c.hits, "subs", c.substitutions, "dels", c.deletions, "ins", c.insertions, "n_ref", sum(len(x) for x in c.references), "n_hyp", sum(len(x) for x in c.hypotheses))

    show_wer_alignment(w)
    show_aligment(ref, pred)

## Oriģinālie Whisper modeļi

| Size   | Parameters | English-only model | Multilingual model | Required VRAM | Relative speed |
|--------|------------|--------------------|---------------------|---------------|----------------|
| tiny   | 39 M       | tiny.en            | tiny                | ~1 GB         | ~10x           |
| base   | 74 M       | base.en            | base                | ~1 GB         | ~7x            |
| small  | 244 M      | small.en           | small               | ~2 GB         | ~4x            |
| medium | 769 M      | medium.en          | medium              | ~5 GB         | ~2x            |
| large  | 1550 M     | N/A                | large               | ~10 GB        | 1x             |
| turbo  | 809 M      | N/A                | turbo               | ~6 GB         | ~8x            |


In [6]:
# Whisper lietošana no komandrindas
!whisper -h

usage: whisper [-h] [--model MODEL] [--model_dir MODEL_DIR] [--device DEVICE]
               [--output_dir OUTPUT_DIR]
               [--output_format {txt,vtt,srt,tsv,json,all}]
               [--verbose VERBOSE] [--task {transcribe,translate}]
               [--language {af,am,ar,as,az,ba,be,bg,bn,bo,br,bs,ca,cs,cy,da,de,el,en,es,et,eu,fa,fi,fo,fr,gl,gu,ha,haw,he,hi,hr,ht,hu,hy,id,is,it,ja,jw,ka,kk,km,kn,ko,la,lb,ln,lo,lt,lv,mg,mi,mk,ml,mn,mr,ms,mt,my,ne,nl,nn,no,oc,pa,pl,ps,pt,ro,ru,sa,sd,si,sk,sl,sn,so,sq,sr,su,sv,sw,ta,te,tg,th,tk,tl,tr,tt,uk,ur,uz,vi,yi,yo,yue,zh,Afrikaans,Albanian,Amharic,Arabic,Armenian,Assamese,Azerbaijani,Bashkir,Basque,Belarusian,Bengali,Bosnian,Breton,Bulgarian,Burmese,Cantonese,Castilian,Catalan,Chinese,Croatian,Czech,Danish,Dutch,English,Estonian,Faroese,Finnish,Flemish,French,Galician,Georgian,German,Greek,Gujarati,Haitian,Haitian Creole,Hausa,Hawaiian,Hebrew,Hindi,Hungarian,Icelandic,Indonesian,Italian,Japanese,Javanese,Kannada,Kazakh,Khmer,Korean,Lao,L

In [7]:
# Whisper turbo modeļa izmantošana; automātiska valodas noteikšana
!whisper zinas1.mp3 --model turbo

100%|█████████████████████████████████████| 1.51G/1.51G [00:22<00:00, 72.7MiB/s]
Detecting language using up to the first 30 seconds. Use `--language` to specify the language
Detected language: Latvian
[00:01.000 --> 00:07.820]  Pirms divām nedēļām negaidīti darbību apturēja Latvijā bāzētā aviokompānija SmartLinks Airlines.
[00:08.180 --> 00:15.940]  Līdzbiedrība, kuras nosaukuma iespējams daļa dzird pirmo reizi, vēl pirms gada tika atzīt par vērtīgāko pašmāju kompānija transporta nozerē.
[00:16.140 --> 00:22.140]  SmartLinks nodarbojās ar pilnu servisu lidmašīnu nomas un čarteru pakalpojamiem visā pasaulē.
[00:22.140 --> 00:30.880]  Kā minēts uzņēmuma mājas lapā, tam bijuši vairāk nekā 500 ofisa un tehniskie darbinieki, kā arī 1300 apkalpas locekļu.


In [8]:
# Mēģinājums ar sistēmas uzvedni uzlabot uzņēmuma nosaukuma atpazīšanu
!whisper zinas1.mp3 --model turbo --initial_prompt "SmartLynx"

Detecting language using up to the first 30 seconds. Use `--language` to specify the language
Detected language: Latvian
[00:00.000 --> 00:07.840]  Pirms divām nedēļām negaidīti darbību apturēja Latvijā bāzētā aviokompānija SmartLynx Airlines.
[00:08.180 --> 00:15.940]  Līdzbiedrība, kuras nosaukuma iespējams daļa dzird pirmo reizi, vēl pirms gada tika atzīt par vērtīgāko pašmāju kompānija transporta nozerē.
[00:16.140 --> 00:22.140]  SmartLynx nodarbojās ar pilnu servisu lidmašīnu nomas un čarteru pakalpojamiem visā pasaulē.
[00:22.140 --> 00:30.880]  Kā minēts uzņēmuma mājas lapā, tam bijuši vairāk nekā 500 ofisa un tehniskie darbinieki, kā arī 1300 apkalpas locekļu.


In [9]:
# Salīdzinājums ar Whisper tiny modeli
!whisper zinas1.mp3 --model tiny

100%|█████████████████████████████████████| 72.1M/72.1M [00:01<00:00, 63.9MiB/s]
Detecting language using up to the first 30 seconds. Use `--language` to specify the language
Detected language: Latvian
[00:00.000 --> 00:08.000]  Pirums divamnēdēļām negājēdīti darbīj baturēlāt vija bazātā avio kompānīs, smartling serlāns.
[00:08.000 --> 00:11.000]  Līdz biedrību kurus no saku minas pēns daļa dzīb pirmu arīs.
[00:11.000 --> 00:16.000]  Elpums gadatīkā dzīt par vērtīgā, ko pašmāj, kompānīt transportu nozere.
[00:16.000 --> 00:22.000]  Smartlings, noderboja, aserpīl, no servis, līdmas šīnu nuomas un charter, pakāl pojimiem visā pasālēt.
[00:22.000 --> 00:31.000]  Kā minēc uzņām mūma maislāpā, tam biji usšīvairāk nekāpiet, sīm tofīs saun techniskie darbīnīja, ka arī tūkstauds trīs, sīmk abkāp sluocekļu.


In [10]:
# Turbo modelis vienmēr atgriež rezultātu oriģinālvalodā, pat ja norādīts "--task translate" parametrs.
# Lai izmantotu Whisper spējas ģenerēt transkripciju angliski, jāizmanto large vai medium modelis.
!whisper zinas1.mp3 --model large-v3 --language lv --task translate

100%|█████████████████████████████████████| 2.88G/2.88G [00:48<00:00, 63.7MiB/s]
[00:00.000 --> 00:08.000]  Two weeks ago, the airline Smartlinks Air Lines, based in Latvia, did not wait for work.
[00:08.000 --> 00:12.000]  The airline, which has been named for the first time for the first time,
[00:12.000 --> 00:16.000]  was named as the most valuable company of transport in the country.
[00:16.000 --> 00:22.000]  Smartlinks worked with full-service airline services and charter services all over the world.
[00:22.000 --> 00:31.000]  As mentioned, the company had more than 500 office and technical staff, as well as 1,300 store windows.


In [11]:
# Whisper lietošana Python kodā
model = whisper.load_model("turbo")

In [12]:
# Ielasa un priekšapstrādā audio paraugu
audio = whisper.load_audio("zinas1.mp3")
audio = whisper.pad_or_trim(audio)

# Sagatavo log-Mel spektrogrammu un pārvieto to uz procesoru, kur ielādēts modelis
mel = whisper.log_mel_spectrogram(audio, n_mels=model.dims.n_mels).to(model.device)

# Nosaka runāto valodu
_, probs = model.detect_language(mel)
print(f"Detected language: {max(probs, key=probs.get)}")

# Dekodē runas datus
options = whisper.DecodingOptions()
result = whisper.decode(model, mel, options)

tokenizer = get_tokenizer(True)
print('Decoded', [tokenizer.encoding.decode([t]) for t in result.tokens])

# Izdrukā transkripciju
print(result)
print(result.text)

Detected language: lv
Decoded ['<|1.02|>', ' Pir', 'ms', ' div', 'ām', ' ned', 'ē', '�', '�', 'ām', ' neg', 'aid', 'ī', 'ti', ' dar', 'b', 'ī', 'bu', ' apt', 'ur', 'ē', 'ja', ' Lat', 'v', 'ij', 'ā', ' b', 'ā', 'z', 'ē', 't', 'ā', ' av', 'i', 'ok', 'omp', 'ān', 'ija', ' Smart', ' Links', ' Airlines', '.', '<|7.84|>', '<|8.20|>', ' L', 'ī', 'dz', 'b', 'ied', 'r', 'ī', 'ba', ',', ' kur', 'as', ' nos', 'au', 'k', 'umi', ' ', 'ies', 'p', 'ē', 'j', 'ams', ' da', '�', '�', 'a', ' dz', 'ird', ' pir', 'mo', ' re', 'izi', ',', ' v', 'ē', 'l', ' pir', 'ms', ' g', 'ada', ' t', 'ika', ' at', 'z', 'ī', 't', ' par', ' v', 'ē', 'rt', 'ī', 'g', 'ā', 'ko', ' pa', 'š', 'm', 'ā', 'ju', ' kom', 'p', 'ān', 'ija', ' transport', 'a', ' no', 'zer', 'ē', '.', '<|15.96|>', '<|16.16|>', ' Smart', ' Links', ' nod', 'ar', 'bo', 'j', 'ā', 's', ' ar', ' pil', 'nu', ' serv', 'isu', ' lid', 'ma', 'š', 'ī', 'nu', ' nom', 'as', ' un', ' č', 'arter', 'u', ' pak', 'al', 'po', 'jam', 'iem', ' vis', 'ā', ' pasa', 'ul', 'ē', 

## Hugging Face modeļu lietošana, novērtēšana

In [13]:
ref = """Aiva Kanepone
Putni brīnās par Liepāju
Kurš liepājnieks gan nezina, ka Liepājā, Zirgu salā, ir putnu vērošanas tornis? Bet kurš ir pamanījis, ka arī putni vēro Liepāju? Brīnās, bola acis un groza galvas, un bezkaunīgi planē pāri kafejnīcu galdiņiem, lai ieskatītos nelidojošo divkāju šķīvjos. Liepājā ir daudz noslēpumaina, par ko brīnīties. Piemēram, naktīs, kad ne tikvien mēness piesprausts pie debesu samta kā zelta ananass, bet arī zvaigznes izbārstītas no Dieva atvilktnēm. Tad tur, lejā, zīriņiem par brīnumu, kaut kas iekvēlojas kā milzīgs ugunskurs, un tam viducī vītero kanārijputniņu bars. „Kas tas ir? Kas tas ir?” sakliedzas kaijas. Tām neviens nav izstāstījis par koncertzāli „Lielais dzintars” un simfonisko orķestri. Vēl viņi nesaprot, kāpēc jaukie Liepājas baznīcu torņi ik pa laikam sajūk prātā un pēkšņi sākas tāda dārdoņa, it kā tajos būtu ielauzušies kazuāri: „Bom! Bom! Bom!”
Un kas notiek Graudu ielas smalkāko namu augstumos? Tur nometas estēti baloži, kas dievina jūgendstilu. Ak, tie lieliskie izciļņi, kur dūdojot griezt mīlas dejas, un iedobumi, kur sastiept liepās salauztos zariņus minimālisma stilā ieturētajām ligzdām!
Kormorāni, viltnieki, jau trešo gadu perina bruņotu laupīšanas uzbrukumu Zivju tirgum Liepājas promenādē, tikai nevar sagaidīt, kad to atkal atvērs. Čurkstes slepeni skatās Liepājas teātra izrādes, bet pēc tam sajūsmā savidžinās. Bet zivju gārņi sapņo, garās kājas cilājot, pastaigāt pa Rožu laukuma dobēm. Diemžēl gārņi kautrējas. Toties vārnai Liepājā ir piemineklis. Karr!
Visskaistākajos vakaros, spārnus plivinādami, putni plecu pie pleca salaižas uz Ziemeļu mola vērot saulrietu. Kormorāns blakus paugurknābja zosij, cekulpīle blakus purva ķauķim, un !pašā galā tārtiņš, no Līvu krasta atlaidies, klusiņām purpina lībiešu valodā.
Rudenī viņi lūr pa Liepājas skolu logiem. Ieraugot gramatiskās kļūdas, saķer apaļās galveles un spalgi čiepst priekšā: „Stulbs nav stūlbs, albums nav albūms, mobilais nav nekāds mobīlais! Čiv!”
Klau, vai tagad arī uz palodzes negrabinās viena zilzīlīte? Ko, ko viņa tur čiepst?
"""

### Novērtējam openai/whisper-tiny

In [14]:
model = pipeline(task="automatic-speech-recognition", model="openai/whisper-tiny")

/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json: 0.00B [00:00, ?B/s]

model.safetensors:   0%|          | 0.00/151M [00:00<?, ?B/s]

generation_config.json: 0.00B [00:00, ?B/s]

tokenizer_config.json: 0.00B [00:00, ?B/s]

...

normalizer.json: 0.00B [00:00, ?B/s]

added_tokens.json: 0.00B [00:00, ?B/s]

special_tokens_map.json: 0.00B [00:00, ?B/s]

preprocessor_config.json: 0.00B [00:00, ?B/s]

Device set to use cuda:0


In [15]:
pred = model('diktats2024.mp3', return_timestamps=True)
pred['text']

Using custom `forced_decoder_ids` from the (generation) config. This is deprecated in favor of the `task` and `language` flags/config options.
Transcription using a multilingual Whisper will default to language detection followed by transcription instead of translation to English. This might be a breaking change for your use case. If you want to instead always translate your audio to English, make sure to pass `language='en'`. See https://github.com/huggingface/transformers/pull/28687 for more details.
Whisper did not predict an ending timestamp, which can happen if audio is cut off in the middle of a word. Also make sure WhisperTimeStampLogitsProcessor was used during generation.


' Ajvākā neponē, potnī brīnās par liapājā. Kūs liapānieks gan nezdīnākā liapājā, zergu salā ir potnumerušanas tuvarnis. Bet kūs ir pamaneis, ka arī potnīt veru liapājā. Brīnās, būl, atsis, un grūs, galvas, un beskā unīgi planējā parikā feinīt, un galdiniem, lai eskatīt uz neliduojošu, djūkāju, štīvijos. Liepājā ir daudz, noslēpā mēn parku, brīnīties. Piemēram naktis, kad ne tikvien menes piesprosts pie, dabas asam pkā zaldā ananas, bet arī zvajīgsnesis bārstītas no dīja vātvilk nēm. Tattur, lēja, zīrņiem per brīnu kautkas iekvēlu eskā milzīgs ugunskurs. Un tam vidu cīvītoru a kanāri putnīņu bārstas. Kas tas ir, kas tas ir saklīdzis kājez. Tam nevienst navistāstējis per konserdzāli lielēs dinters un symfonis ko Ortestri. Vēl viņi nesaprūt kapēc jau kēlības, baznīt sturni, ikpalēkam sa jūk prata, un peksņu sakas tāda darduņa. Tajos būtu, ila uz uzšies, ka zlāri, bāmu, bāmu, bāmu, bāmu, bāmu, bāmu, bāmu, bāmu, bāmu, bāmu, bāmu, bāmu, bāmu, bāmu, bāmu, bāmu, bāmu, bāmu, bāmu, bāmu, bāmu, b

In [16]:
evaluate(ref, pred['text'])

WER 1.0436241610738255 hits 49 subs 245 dels 4 ins 62 n_ref 298 n_hyp 356
CER 0.6471774193548387 hits 1335 subs 565 dels 84 ins 635 n_ref 1984 n_hyp 2535


### Novērtējam openai/whisper-large-v3-turbo

In [17]:
model = pipeline(task="automatic-speech-recognition", model="openai/whisper-large-v3-turbo")

config.json: 0.00B [00:00, ?B/s]

model.safetensors:   0%|          | 0.00/1.62G [00:00<?, ?B/s]

generation_config.json: 0.00B [00:00, ?B/s]

tokenizer_config.json: 0.00B [00:00, ?B/s]

vocab.json: 0.00B [00:00, ?B/s]

...

normalizer.json: 0.00B [00:00, ?B/s]

added_tokens.json: 0.00B [00:00, ?B/s]

special_tokens_map.json: 0.00B [00:00, ?B/s]

preprocessor_config.json:   0%|          | 0.00/340 [00:00<?, ?B/s]

Device set to use cuda:0


In [18]:
pred = model('diktats2024.mp3', return_timestamps=True)
pred['text']

' Aiva Kanepone putni brīnās par liepāju. Kurš liepājnieks gan nezina, ka liepājā zirgu salā ir putnu vērošanas tornis, bet kurš ir pamanījis, ka arī putni vēro liepāju. Brīnās bola acis un groza galvas Un bezkaunīgi planē pāri kafeinīcu galdiņiem Lai ieskatītos nelidojošo divkāju šķīvjos Liepājā ir daudz noslēpumainu par ko brīnīties Piemēram naktīs, kad ne tik vien mēnesis Piesprausts pie debesu samta kā zelta ananas bet arī zvaigznes izbārstītas no dieva atvilknēm. Tad tur, lejā, zīriņiem par brīnumu, kaut kas iekvēlojas kā milzīgs ugunskurs un tam viducī vītero kanārī putniņu bars. Kas tas ir? Kas tas ir? sakliedzis kā ejas. Tām neviens nav izstāstījis par koncertzāli lielais dzintars un simfonisko orķestri Vēl viņi nesaprot, kāpēc jaukie liepājas baznītes tūrņi ik pa laikam sajūk prātā Un pēkšņi sākas tāda dārdoņa, it kā tajos būtu ielauzušies kazuāri BOM! BOM! BOM! Un kas notiek graudu ielas smalkāko namu augstumos? Tur nometas estēti baloži, kas dievina jūgenstil. Ak, tie lielis

In [19]:
evaluate(ref, pred['text'])

WER 0.12751677852348994 hits 264 subs 32 dels 2 ins 4 n_ref 298 n_hyp 300
CER 0.024193548387096774 hits 1948 subs 25 dels 11 ins 12 n_ref 1984 n_hyp 1985


### Novērtējam facebook/mms-1b-all

In [20]:
model = pipeline(task="automatic-speech-recognition", model="facebook/mms-1b-all")

config.json: 0.00B [00:00, ?B/s]

model.safetensors:   0%|          | 0.00/3.86G [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/397 [00:00<?, ?B/s]

vocab.json: 0.00B [00:00, ?B/s]

special_tokens_map.json:   0%|          | 0.00/96.0 [00:00<?, ?B/s]

preprocessor_config.json:   0%|          | 0.00/254 [00:00<?, ?B/s]

Device set to use cuda:0


In [21]:
pred = model('diktats2024.mp3', generate_kwargs={"language": "lav", "task": "transcribe"}, chunk_length_s=30, stride_length_s=5)
pred['text']

'aiva kanepone putni brins par liepju kur liepajnieks gan nezina ka liepaja zirgu sala ir putnu vroanas tornis bet kurs ir pamanijis ka ari putni vero liepaju brins bola acis un groza galvas un bezkaunigi plane pri kafeinicu galdiniem lai ieskatitos nelidojoo diukaju stivjos liepja ir daudz noslepumaini par ko brinties piemram naktis kad ne tikvien menests piesprausts pie debesa samta ka zelta ananass bet ari zvaigznes izbarstitas no dieva atvilknem tad tur leja ziriniem par brinumu kaut kas iekvelojas ka milzigs ugunskurs un tam viducivitero kanri putninu bars kas tas ir kas tas ir sakliedzas kailas tam neviens nav izststijis par koncertzali lielais dzinters un simfonisko ortestri vel vini nesaprot kapec jaukie liepajas baznicas turni ikpalaikam sajuk prata un peknis sakas tada dardona itk tajos butu ielauzuies kazuari bom bo bo un kas notiek graudu ielast smalkko namu augstumos tur nometas estti baloi kas dievina jugenstil ak tie lieliskie izcilni kur dudojot griezt milas dejas un ie

In [22]:
evaluate(ref, pred['text'])

WER 0.5335570469798657 hits 140 subs 153 dels 5 ins 1 n_ref 298 n_hyp 294
CER 0.10887096774193548 hits 1774 subs 157 dels 53 ins 6 n_ref 1984 n_hyp 1937


## ASR demo saskarne

In [23]:
model = pipeline(task="automatic-speech-recognition", model="openai/whisper-large-v3-turbo")

Device set to use cuda:0


In [24]:
def transcribe(audio):
    pred = model(audio, return_timestamps=True)
    print(pred)
    return pred.get("text", str(result))

gr.Interface(
    title="ASR demo",
    fn=transcribe,
    inputs=gr.Audio(sources=["microphone", "upload"], type="filepath"),
    outputs=gr.Textbox(),
).launch(share=True, debug=True)

# Lai veiktu ierakstīšanu no mikrofona, pārlūkā jāatver saite, kas šī koda izpildes laikā tiks uzģenerēta.
# Pārbaudīts ar Chrome (jāatļauj izmantot mikrofonu).
# Audio faila augšupielāde un transkribēšana var tikt darbināta tepat Colab vidē.

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://271738cf3ec4324b02.gradio.live

This share link expires in 1 week. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://271738cf3ec4324b02.gradio.live


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [25]:
# Lejupielādējam diktāta tekstu
!wget https://raw.githubusercontent.com/LUMII-AILab/NLP_Course/refs/heads/main/notebooks/resources/ASR/diktats2024.txt

# Nolasām faila saturu
with open("diktats2024.txt", "r", encoding="utf-8") as f:
    ref_text = f.read()

print("References teksts ielādēts (sākums):", ref_text[:100])

--2026-01-21 20:26:03--  https://raw.githubusercontent.com/LUMII-AILab/NLP_Course/refs/heads/main/notebooks/resources/ASR/diktats2024.txt
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 2258 (2.2K) [text/plain]
Saving to: ‘diktats2024.txt’

diktats2024.txt     100%[===================>]   2.21K  --.-KB/s    in 0s      

2026-01-21 20:26:03 (48.2 MB/s) - ‘diktats2024.txt’ saved [2258/2258]

References teksts ielādēts (sākums): Aiva Kanepone
Putni brīnās par Liepāju
Kurš liepājnieks gan nezina, ka Liepājā, Zirgu salā, ir putnu


In [26]:
from transformers import pipeline

# 1. Ielādējam AiLab pielāgoto Whisper modeli
# https://huggingface.co/AiLab-IMCS-UL/whisper-large-v3-lv-late-cv19
print("Ielādē AiLab Whisper modeli...")
ailab_whisper = pipeline("automatic-speech-recognition", model="AiLab-IMCS-UL/whisper-large-v3-lv-late-cv19", device=0)

# 2. Veicam transkripciju diktātam
# generate_kwargs={"language": "latvian"} palīdz modelim saprast kontekstu, lai gan whisper-lv jau ir trenēts uz latviešu valodu
print("Notiek transkripcija...")
pred_whisper = ailab_whisper("diktats2024.mp3", generate_kwargs={"language": "latvian", "task": "transcribe"}, return_timestamps=True)

# 3. Izdrukājam rezultātu un aprēķinām WER
print("\n--- AiLab Whisper Rezultāti ---")
# Mēs izmantojam pred_whisper['text'], jo pipeline atgriež vārdnīcu
evaluate(ref_text, pred_whisper['text'])

Ielādē AiLab Whisper modeli...


config.json: 0.00B [00:00, ?B/s]

model.safetensors:   0%|          | 0.00/3.22G [00:00<?, ?B/s]

generation_config.json: 0.00B [00:00, ?B/s]

tokenizer_config.json: 0.00B [00:00, ?B/s]

...

added_tokens.json: 0.00B [00:00, ?B/s]

special_tokens_map.json: 0.00B [00:00, ?B/s]

preprocessor_config.json:   0%|          | 0.00/340 [00:00<?, ?B/s]

Device set to use cuda:0


Notiek transkripcija...

--- AiLab Whisper Rezultāti ---
WER 0.06711409395973154 hits 281 subs 16 dels 1 ins 3 n_ref 298 n_hyp 300
CER 0.014616935483870967 hits 1968 subs 11 dels 5 ins 13 n_ref 1984 n_hyp 1992


In [27]:
# 1. Ielādējam AiLab Wav2Vec2 modeli
# https://huggingface.co/AiLab-IMCS-UL/wav2vec-xls-r-300m-lv-cv17
print("Ielādē AiLab Wav2Vec modeli...")
ailab_wav2vec = pipeline("automatic-speech-recognition", model="AiLab-IMCS-UL/wav2vec-xls-r-300m-lv-cv17", device=0)

# 2. Veicam transkripciju
# Wav2Vec modeļiem parasti nav vajadzīgs norādīt valodu vai task parametrus tādā veidā kā Whisper
print("Notiek transkripcija...")
pred_wav2vec = ailab_wav2vec("diktats2024.mp3")

# 3. Izdrukājam rezultātu un aprēķinām WER
print("\n--- AiLab Wav2Vec Rezultāti ---")
evaluate(ref_text, pred_wav2vec['text'])

Ielādē AiLab Wav2Vec modeli...


config.json: 0.00B [00:00, ?B/s]

pytorch_model.bin:   0%|          | 0.00/1.26G [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/1.26G [00:00<?, ?B/s]

tokenizer_config.json: 0.00B [00:00, ?B/s]

...

added_tokens.json:   0%|          | 0.00/60.0 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/96.0 [00:00<?, ?B/s]

preprocessor_config.json:   0%|          | 0.00/214 [00:00<?, ?B/s]

Device set to use cuda:0


Notiek transkripcija...

--- AiLab Wav2Vec Rezultāti ---
WER 0.2181208053691275 hits 234 subs 46 dels 18 ins 1 n_ref 298 n_hyp 281
CER 0.03477822580645161 hits 1919 subs 24 dels 41 ins 4 n_ref 1984 n_hyp 1947


# Pedejais uzdevums

In [28]:
# YT paraugs pedejam uzdevumam
!yt-dlp -x --audio-format mp3 --download-sections "*00:01:02-00:05:10"  -o "naves_ena_4min.%(ext)s" "https://www.youtube.com/watch?v=GeeyY4088d0"

[youtube] Extracting URL: https://www.youtube.com/watch?v=GeeyY4088d0
[youtube] GeeyY4088d0: Downloading webpage
[youtube] GeeyY4088d0: Downloading android sdkless player API JSON
[youtube] GeeyY4088d0: Downloading web safari player API JSON
[youtube] GeeyY4088d0: Downloading m3u8 information
[info] GeeyY4088d0: Downloading 1 format(s): 251
[info] GeeyY4088d0: Downloading 1 time ranges: 62.0-310.0
[download] Destination: naves_ena_4min.webm
Input #0, matroska,webm, from 'https://rr3---sn-qxoednes.googlevideo.com/videoplayback?expire=1769048936&ei=CDdxaZ6jA8upsfIP8t3UkAU&ip=34.182.48.118&id=o-AMKbB0Jh4hVqxwyeb0jVccfZR7rRKdIFkLgVjgqTbpHO&itag=251&source=youtube&requiressl=yes&xpc=EgVo2aDSNQ%3D%3D&cps=3&met=1769027336%2C&mh=NF&mm=31%2C26&mn=sn-qxoednes%2Csn-a5msenle&ms=au%2Conr&mv=m&mvi=3&pl=17&rms=au%2Cau&initcwndbps=4967500&bui=AW-iu_pUUxDCPHDGmoogPMR0Fv9Q_jLIi4_44FhtqcsvIAXC_KgHfzzYISfXN-WwBXJegTDSJypHupyu&spc=q5xjPKDR4KhK&vprv=1&svpuc=1&mime=audio%2Fwebm&rqh=1&gir=yes&clen=64030959&du

In [29]:
# @title Default title text
display(Audio('naves_ena_4min.mp3'))

In [32]:
# 1. Nolasām tavu manuāli sagatavoto references tekstu
# Pārliecinies, ka fails "naves_ena_4min.txt" ir augšupielādēts Colab failu sadaļā (kreisajā pusē)
filename = "naves_ena_4min.txt"

try:
    with open(filename, "r", encoding="utf-8") as f:
        my_ref_text = f.read()
    print(f"References teksts veiksmīgi nolasīts. Garums: {len(my_ref_text)} simboli.")
except FileNotFoundError:
    print(f"Kļūda: Fails '{filename}' netika atrasts. Lūdzu, augšupielādē to Colab vidē.")
    my_ref_text = ""

# 2. Veicam transkripciju un novērtēšanu (tikai, ja teksts ir nolasīts)
if my_ref_text:
    # Izmantojam iepriekš definēto 'ailab_whisper' modeli.
    # Garākiem failiem (4 min) ieteicams pievienot chunk_length_s, lai modelis sadalītu audio gabalos.
    print("Notiek transkripcija ar AiLab Whisper modeli...")

    # Piezīme: 'ailab_whisper' mainīgajam jābūt definētam iepriekšējos koda blokos
    # mans_rezultats = ailab_whisper(
    #     "naves_ena_4min.mp3",
    #     generate_kwargs={"language": "latvian", "task": "transcribe"},
    #     chunk_length_s=30
    # )

    mans_rezultats = ailab_whisper("naves_ena_4min.mp3", generate_kwargs={"language": "latvian", "task": "transcribe"}, return_timestamps=True)


    # 3. Izdrukājam rezultātu un WER metriku
    print("\n--- Mana video novērtējums (WER) ---")
    evaluate(my_ref_text, mans_rezultats['text'])

References teksts veiksmīgi nolasīts. Garums: 2965 simboli.
Notiek transkripcija ar AiLab Whisper modeli...

--- Mana video novērtējums (WER) ---
WER 0.10212765957446808 hits 427 subs 42 dels 1 ins 5 n_ref 470 n_hyp 474
CER 0.02719886965736489 hits 2802 subs 20 dels 9 ins 48 n_ref 2831 n_hyp 2870
